# Изучение и предобработка данных

# <a id="0">Содержание</a>

- <a href="#1">Открытие данных и их описание</a>
- <a href="#2">Предобработка данных. Добавление признаков</a>  
    - <a href="#21">Обработка дубликатов</a>
    - <a href="#22">Обработка категориальных и временных признаков</a>
    - <a href="#23">Поиск и обработка аномалий в данных</a>
    - <a href="#24">Добавление новых признаков</a>
- <a href="#3">Разведывательный анализ данных</a>  
- <a href="#4">Выводы</a>  

In [173]:
# Импортируем необходимые библиотеки
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

from ydata_profiling import ProfileReport 
from ydata_profiling.config import Settings
import numpy as np

# <a id="1">Открытие данных и их описание</a>

Загрузим все данные

In [174]:
# Откроем данные
users = pd.read_csv('../src/users.tsv', sep='\t')
history = pd.read_csv('../src/history.tsv', sep='\t')
validate = pd.read_csv('../src/validate.tsv', sep='\t')
validate_answers = pd.read_csv('../src/validate_answers.tsv', sep='\t')

In [175]:
# Посмотрим информацию о датасете
users.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27769 entries, 0 to 27768
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype
---  ------   --------------  -----
 0   user_id  27769 non-null  int64
 1   sex      27769 non-null  int64
 2   age      27769 non-null  int64
 3   city_id  27769 non-null  int64
dtypes: int64(4)
memory usage: 867.9 KB


In [176]:
# Рассмотрим первые 5 строк
users.head()

user_id  sex  age  city_id
0        0    2   19        0
1        1    1    0        1
2        2    2   24        2
3        3    1   20        3
4        4    2   29        4

In [ ]:
profile = ProfileReport(users, title="Profiling Report 'users'")
profile.to_file("Profiling Report users.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
profile.to_html()

`users.tsv`:
- `user_id` – уникальный идентификатор пользователя
- `sex` – указанный пользователем пол в анкете
- `age` – указанный пользователем в анкете возраст пользователя. 0 – не указан.
- `city_id` - указанный пользователем в анкете город проживания. 0 – не указан.

В датасете информация о 27 769  пользователях. Пропуски отсутствуют

In [6]:
# Посмотрим информацию о датасете
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1147857 entries, 0 to 1147856
Data columns (total 4 columns):
 #   Column     Non-Null Count    Dtype  
---  ------     --------------    -----  
 0   hour       1147857 non-null  int64  
 1   cpm        1147857 non-null  float64
 2   publisher  1147857 non-null  int64  
 3   user_id    1147857 non-null  int64  
dtypes: float64(1), int64(3)
memory usage: 35.0 MB


In [7]:
# Рассмотрим первые 5 строк
history.head()

hour     cpm  publisher  user_id
0    10   30.00          1    15661
1     8   41.26          1     8444
2     7  360.00          1    15821
3    18  370.00          1    21530
4     8  195.00          2    22148

In [9]:
profile = ProfileReport(history, title="Profiling Report 'history'")
profile.to_file("Profiling Report history.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

`history.tsv`:
- `hour` – в какой час пользователь видел объявление
- `cpm` - цена показанного рекламного объявления в рекламном аукционе. Это значит, что на данном аукционе это была максимальная ставка. 
- `publisher` - площадка, на который пользователь видел рекламу
- `user_id` - уникальный идентификатор пользователя

В датасете 1 147 857 строк. Причем в столбце `hour` не дата с конкретным часом, а только час. Пропусков нет

In [21]:
# Посмотрим информацию о датасете
validate.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1008 entries, 0 to 1007
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   cpm            1008 non-null   float64
 1   hour_start     1008 non-null   int64  
 2   hour_end       1008 non-null   int64  
 3   publishers     1008 non-null   object 
 4   audience_size  1008 non-null   int64  
 5   user_ids       1008 non-null   object 
dtypes: float64(1), int64(3), object(2)
memory usage: 47.4+ KB


In [23]:
# Рассмотрим первые 5 строк
validate.head()

cpm  hour_start  hour_end     publishers  audience_size  \
0  220.0        1058      1153           7,17           1906   
1  312.0        1295      1301           3,18           1380   
2   70.0        1229      1249  1,2,3,9,15,21            888   
3  240.0        1295      1377           1,14            440   
4  262.0         752       990        1,3,7,8           1476   

                                            user_ids  
0  12,44,46,50,58,71,93,122,134,143,176,184,187,1...  
1  29,81,98,102,165,167,195,205,218,231,242,263,3...  
2  12,23,25,29,45,85,92,124,156,190,272,334,456,5...  
3  44,122,187,209,242,255,312,345,382,465,513,524...  
4  15,24,30,43,50,53,96,105,159,168,181,190,196,2...

In [10]:
profile = ProfileReport(validate[['cpm', 'hour_start', 'hour_end', 'publishers', 'audience_size']], title="Profiling Report 'validate'")
profile.to_file("Profiling Report validate.html")
profile.to_notebook_iframe()

/Users/bair/miniconda3/envs/my_env/lib/python3.12/site-packages/ydata_profiling/utils/dataframe.py:137: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.rename(columns={"index": "df_index"}, inplace=True)


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

`validate.tsv`:
- `cpm` - для какой цены объявления нужно сделать прогноз
- `hour_start` - предположительное время запуска рекламного объявления
- `hour_end` - предположительное время остановки рекламного объявления. По итогу прогноз делается для рекламного объявление, которое будет запущено в период времени `[hour_start, hour_end]`
- `publishers` - на каких площадках объявление может быть показано
- `audience_size` - размер аудитории объявления, количество идентификаторов в поле `user_ids`
- `user_ids` – аудитория объявления – список пользователей, кому рекламодатель хочет показать объявление.

В датасете 1008 строк. Проупсков нет

In [24]:
# Посмотрим информацию о датасете
validate_answers.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1008 entries, 0 to 1007
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   at_least_one    1008 non-null   float64
 1   at_least_two    1008 non-null   float64
 2   at_least_three  1008 non-null   float64
dtypes: float64(3)
memory usage: 23.8 KB


In [25]:
# Рассмотрим первые 5 строк
validate_answers.head()

at_least_one  at_least_two  at_least_three
0        0.0430        0.0152          0.0073
1        0.0130        0.0000          0.0000
2        0.0878        0.0135          0.0000
3        0.2295        0.1295          0.0727
4        0.3963        0.2785          0.2270

In [11]:
profile = ProfileReport(validate_answers, title="Profiling Report 'validate_answers'")
profile.to_file("Profiling Report validate_answers.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

`validate_answers.tsv`:
- `at_least_one` - доля пользователей, которая увидит объявление хотя бы один раз
- `at_least_two` - доля пользователей, которая увидит объявление хотя бы два раза
- `at_least_three` - доля пользователей, которая увидит объявление хотя бы три раза

В датасете также 1008 строк. Пропусков нет

# <a id="2">Предобработка данных. Добавление признаков</a>
## <a href="#21">Обработка дубликатов</a>

В данных содержится довольно большой процент неопределенности по пользователям, например, в 30% случаев мы не знаем город респондента, на данном этаме избавлятся от столько большого куска данных нет смысла, возмонжо признак города не будет включен в обучающую выборку

В Датасете history мы можем увидеть дубликаты (18811), удалим их

In [177]:
history = history.drop_duplicates()

## <a href="#22">Обработка категориальных и временных признаков</a>

Когда проводится таргетриование целевой аудитории для рекламы обычно используется понятие возрастной группы, а не конкретный возраст, поэтому пользователей можно поделиь на возрастные группы исходя из представленной фичи 

In [178]:
users['age_categorized'] = users['age'].apply(lambda x: 0 if x == 0 else int(x) // 10 + 1)
users['age_categorized']

0        2
1        0
2        3
3        3
4        3
        ..
27764    4
27765    4
27766    3
27767    2
27768    4
Name: age_categorized, Length: 27769, dtype: int64

## <a href="#23">Поиск и обработка аномалий в данных</a>

Исходя из разспределения пользователей, можем увидеть что часть из них находится в категории 80+ и даже 100+. Возраст является таже важной характеристикой для определения интересов респондента и вероятности показа то или иной рекламы. Подобная информация обычно нерепрезентативна для оценивания, так как с немалой долей вероятности пользователь находится подростковой возрастной категории (условно от 10 до 20 лет) Однако предположение что пользователь точно подросток весьма смелое, и изменение возрастной группы может сильно сказаться на качестве модели. Посмотрим, сколько суммарно пользователей находятся в категории 80+

In [179]:
len(users[users['age'] > 80])

632

Также стоит отметить что пол респондентов указан практически везде за 3 исключением 30 респондентов, пол человека весьма существенный показатель для определение интересов для таргетирования, в этом случае мы можем избавиться от шумных данных


In [180]:
users = users[users['age'] <= 80]
len(users)

27137

Можно видеть аномальные данные в колонке стоимости рекламы в исторических данных, они могут внести неточность при нормализации. Также стоит учесть, что выборка планируемой к показу рекламы имеет разброс цены до 500, следовательно нам не нужны исторические данные со стоимостью рекламы выше 500, проверим сколько таких данных и удалим их 

In [181]:
len(history[history['cpm'] > 500])

70829

In [182]:
history = history[history['cpm'] <= 500]
len(history)

1054838

## <a href="#24">Добавление новых признаков</a>

Выборку истории можно расшироить данными о каждом пользовтеле

In [183]:
history = history.merge(users, on='user_id', how='left')
history.head()

hour     cpm  publisher  user_id  sex   age  city_id  age_categorized
0    10   30.00          1    15661  2.0  28.0     68.0              3.0
1     8   41.26          1     8444  1.0  41.0      0.0              5.0
2     7  360.00          1    15821  1.0  24.0      0.0              3.0
3    18  370.00          1    21530  2.0  17.0     13.0              2.0
4     8  195.00          2    22148  1.0  23.0      7.0              3.0

In [184]:
history.drop(['age'], axis=1, inplace=True)
history.head()

hour     cpm  publisher  user_id  sex  city_id  age_categorized
0    10   30.00          1    15661  2.0     68.0              3.0
1     8   41.26          1     8444  1.0      0.0              5.0
2     7  360.00          1    15821  1.0      0.0              3.0
3    18  370.00          1    21530  2.0     13.0              2.0
4     8  195.00          2    22148  1.0      7.0              3.0

Также стоит привести поля 'sex' и 'city_id' к целочисленному формату

In [185]:
history['sex'].unique()

array([ 2.,  1., nan,  0.])

In [186]:
history['sex'] = history['sex'].astype('Int64')
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1054838 entries, 0 to 1054837
Data columns (total 7 columns):
 #   Column           Non-Null Count    Dtype  
---  ------           --------------    -----  
 0   hour             1054838 non-null  int64  
 1   cpm              1054838 non-null  float64
 2   publisher        1054838 non-null  int64  
 3   user_id          1054838 non-null  int64  
 4   sex              1028410 non-null  Int64  
 5   city_id          1028410 non-null  float64
 6   age_categorized  1028410 non-null  float64
dtypes: Int64(1), float64(3), int64(3)
memory usage: 57.3 MB


In [188]:
len(history[history['sex'] == 0])

51

In [189]:
history = history[history['sex'] != 0]

In [190]:
history['city_id'] = history['city_id'].astype('Int64')
history.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1028359 entries, 0 to 1054837
Data columns (total 7 columns):
 #   Column           Non-Null Count    Dtype  
---  ------           --------------    -----  
 0   hour             1028359 non-null  int64  
 1   cpm              1028359 non-null  float64
 2   publisher        1028359 non-null  int64  
 3   user_id          1028359 non-null  int64  
 4   sex              1028359 non-null  Int64  
 5   city_id          1028359 non-null  Int64  
 6   age_categorized  1028359 non-null  float64
dtypes: Int64(2), float64(2), int64(3)
memory usage: 64.7 MB


Нам необходимо нормализоват данные по cpm для лучшего обучения, для этого выясним, какая максимальная стоимость рекламы в валидационной выборке


In [191]:
cpmMaxValidate = max(validate['cpm'])
cpmMaxHistory = max(history['cpm'])
print(f'validate - {cpmMaxValidate}, history - {cpmMaxHistory}')

validate - 475.0, history - 500.0


Посчитаем количество данных со стоимостью рекламы выше 475 в датасете истории

In [192]:
len(history[history['cpm'] > 475])

8144

Удалим эти данные для правильной нормализации истории и валидации

In [193]:
history = history[history['cpm'] <= 475 ]
len(history['cpm'])

1020215

Произведем нормализацию данных 

In [194]:
history['cpm'] = history['cpm']  / history['cpm'].max() 
validate['cpm'] = validate['cpm'] / validate['cpm'].max()

In [195]:
history.head()

hour       cpm  publisher  user_id  sex  city_id  age_categorized
0    10  0.063158          1    15661    2       68              3.0
1     8  0.086863          1     8444    1        0              5.0
2     7  0.757895          1    15821    1        0              3.0
3    18  0.778947          1    21530    2       13              2.0
4     8  0.410526          2    22148    1        7              3.0

Проверим временной промежуток показа рекламы в истоическом датасете и валидационном дата сете

In [196]:
minHourHistory = history['hour'].min()
maxHourHistory = history['hour'].max()

minHourValidate = validate['hour_start'].min()
maxHourValidate = validate['hour_end'].max()

print(f'history min = {minHourHistory}, history max = {maxHourHistory}, validate min = {minHourValidate}, validate max = {maxHourValidate}')

history min = 3, history max = 1490, validate min = 747, validate max = 1488


Нормализуем данные в истории, используем максимальный час в обоих датасетах - 1490

In [197]:
normalizeCoef = maxHourHistory

history['hour'] = history['hour'] / normalizeCoef

Нормализация часов в валидационной вборке будет прведена после нормализации датасета в целом

В датасете валидации присутсвуют поля, которые тяжело интерпретировть при обучении, изменим структуру валидационного датасета

1. Нужно разделить пользователей
2. Нужно разбить площадки

In [ ]:
validate_test = validate.set_index(['cpm', 'hour_start', 'hour_end', 'publishers', 'audience_size'])['user_ids'].str.split(',', expand = True).stack().reset_index(level = 5, drop = True).reset_index(name = 'user_ids')
validate_test.head()

cpm  hour_start  hour_end     publishers  audience_size  \
0  0.463158        1058      1153           7,17           1906   
1  0.656842        1295      1301           3,18           1380   
2  0.147368        1229      1249  1,2,3,9,15,21            888   
3  0.505263        1295      1377           1,14            440   
4  0.551579         752       990        1,3,7,8           1476   

                                            user_ids  
0  12,44,46,50,58,71,93,122,134,143,176,184,187,1...  
1  29,81,98,102,165,167,195,205,218,231,242,263,3...  
2  12,23,25,29,45,85,92,124,156,190,272,334,456,5...  
3  44,122,187,209,242,255,312,345,382,465,513,524...  
4  15,24,30,43,50,53,96,105,159,168,181,190,196,2...

In [199]:
len(validate_test)

1098808

In [200]:
validate_test = validate_test.set_index(['cpm', 'hour_start', 'hour_end', 'audience_size', "user_ids"])['publishers'].str.split(',', expand = True).stack().reset_index(level = 5, drop = True).reset_index(name = 'publishers')
validate_test.head(15)

cpm  hour_start  hour_end  audience_size user_ids publishers
0   0.463158        1058      1153           1906       12          7
1   0.463158        1058      1153           1906       12         17
2   0.463158        1058      1153           1906       44          7
3   0.463158        1058      1153           1906       44         17
4   0.463158        1058      1153           1906       46          7
5   0.463158        1058      1153           1906       46         17
6   0.463158        1058      1153           1906       50          7
7   0.463158        1058      1153           1906       50         17
8   0.463158        1058      1153           1906       58          7
9   0.463158        1058      1153           1906       58         17
10  0.463158        1058      1153           1906       71          7
11  0.463158        1058      1153           1906       71         17
12  0.463158        1058      1153           1906       93          7
13  0.463158        1058      1153           1906       93         17
14  0.463158        1058      1153           1906      122          7

In [201]:
validate_test['hour_start'] = validate_test['hour_start'] / normalizeCoef
validate_test['hour_end'] = validate_test['hour_end'] / normalizeCoef
validate_test.head()

cpm  hour_start  hour_end  audience_size user_ids publishers
0  0.463158    0.710067  0.773826           1906       12          7
1  0.463158    0.710067  0.773826           1906       12         17
2  0.463158    0.710067  0.773826           1906       44          7
3  0.463158    0.710067  0.773826           1906       44         17
4  0.463158    0.710067  0.773826           1906       46          7

In [202]:
validate_test['user_id'] = validate_test['user_ids'].astype('Int64')
validate_test['publisher'] = validate_test['publishers'].astype('Int64')


In [204]:
validate_test.drop(['user_ids', 'publishers'], inplace=True, axis=1)

In [205]:
validate_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3815987 entries, 0 to 3815986
Data columns (total 6 columns):
 #   Column         Dtype  
---  ------         -----  
 0   cpm            float64
 1   hour_start     float64
 2   hour_end       float64
 3   audience_size  int64  
 4   user_id        Int64  
 5   publisher      Int64  
dtypes: Int64(2), float64(3), int64(1)
memory usage: 182.0 MB


Проверим зависимости в результирующем датасете

In [206]:
validate_test.corr(method='pearson')

cpm  hour_start  hour_end  audience_size   user_id  \
cpm            1.000000    0.020599  0.027140      -0.017746 -0.000326   
hour_start     0.020599    1.000000  0.786625       0.005846  0.000427   
hour_end       0.027140    0.786625  1.000000       0.010611 -0.000300   
audience_size -0.017746    0.005846  0.010611       1.000000 -0.001953   
user_id       -0.000326    0.000427 -0.000300      -0.001953  1.000000   
publisher      0.001646    0.010081  0.003453       0.034048 -0.000104   

               publisher  
cpm             0.001646  
hour_start      0.010081  
hour_end        0.003453  
audience_size   0.034048  
user_id        -0.000104  
publisher       1.000000

In [207]:
validate_test['normalized_mean_hour'] = (validate_test['hour_start'] + validate_test['hour_end'])/2
validate_test.head()

cpm  hour_start  hour_end  audience_size  user_id  publisher  \
0  0.463158    0.710067  0.773826           1906       12          7   
1  0.463158    0.710067  0.773826           1906       12         17   
2  0.463158    0.710067  0.773826           1906       44          7   
3  0.463158    0.710067  0.773826           1906       44         17   
4  0.463158    0.710067  0.773826           1906       46          7   

   normalized_mean_hour  
0              0.741946  
1              0.741946  
2              0.741946  
3              0.741946  
4              0.741946

# <a id="3">Разведывательный анализ данных</a>

# <a id="4">Выводы</a>

In [ ]:
users.to_csv("users_preprocessed.csv")
history.to_csv("history_preprocessed.csv")
validate_test.to_csv("validate_preprocessed.csv")